<a href="https://colab.research.google.com/github/bhavya-rema/E-Commerce-Recommendation/blob/main/recommendation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
# ! wget https://github.com/neo4j/graph-data-science/releases/download/1.8.2/neo4j-graph-data-science-1.8.2-standalone.zip
# ! unzip neo4j-graph-data-science-1.8.2-standalone.zip
# ! sudo cp  neo4j-graph-data-science-1.8.2.jar /var/lib/neo4j/plugins
# ! sudo sh -c 'echo dbms.security.procedures.unrestricted=gds.* >> /etc/neo4j/neo4j.conf'
# ! sudo sh -c 'echo dbms.security.procedures.allowlist=gds.* >> /etc/neo4j/neo4j.conf'

In [ ]:
!pip install neo4j

In [ ]:
from IPython.display import display
import pandas as pd
import numpy as np
from tqdm import tqdm
from neo4j import GraphDatabase
from neo4j.exceptions import ClientError

In [ ]:
#standalone version
bolt_url = "bolt://localhost:7687"
user = "neo4j"
password = "neo3j"
driver = GraphDatabase.driver(bolt_url, auth=(user, password))
session = driver.session()

In [ ]:
with driver.session() as session:
    greeting = session.run("""
    SHOW DATABASES
    """)
    for row in greeting:
        print(row)

<Record name='neo4j' aliases=[] access='read-write' address='localhost:7687' role='standalone' requestedStatus='online' currentStatus='online' error='' default=True home=True>
<Record name='system' aliases=[] access='read-write' address='localhost:7687' role='standalone' requestedStatus='online' currentStatus='online' error='' default=False home=False>


In [ ]:
#sandbox version
# bolt_url = "bolt://3.239.62.158:7687"
# user = "neo4j"
# password = "majority-top-athwartship"
# driver = GraphDatabase.driver(bolt_url, auth=(user, password))
# session = driver.session()

In [ ]:
!pip install neo4j sklearn altair

Graphsage Implementation

In [ ]:
cb_df = pd.read_pickle('cust_behaviour_updated.pkl')
print(cb_df.shape)
display(cb_df.head())

(65180535, 9)


event_time event_type                        category_code  \
1  2019-10-01 00:00:00 UTC       view  appliances.environment.water_heater   
3  2019-10-01 00:00:01 UTC       view                   computers.notebook   
4  2019-10-01 00:00:04 UTC       view               electronics.smartphone   
5  2019-10-01 00:00:05 UTC       view                    computers.desktop   
8  2019-10-01 00:00:10 UTC       view                   apparel.shoes.keds   

    brand    price    user_id                          user_session  \
1    aqua    33.20  554748717  9333dfbd-b87a-4708-9857-6336556b0fcc   
3  lenovo   251.74  550050854  7c90fc70-0e80-4590-96f3-13c02c18c713   
4   apple  1081.98  535871217  c6bd7419-2748-4c56-95b4-8cec9ff8b80d   
5  pulser   908.62  512742880  0d0d91c2-c9c2-4e81-90a5-86594dec0db9   
8   baden   102.71  520571932  ac1cd4e5-a3ce-4224-a2d7-ff660a105880   

               bins  product_id  
1      (30.0, 40.0]        2735  
3    (250.0, 260.0]       13815  
4  (1080.0, 1090.0]       21204  
5    (900.0, 910.0]       13010  
8    (100.0, 110.0]        1066

In [ ]:
!zip -r cust_behaviour.zip ./cust_behaviour_updated.pkl

  adding: cust_behaviour_updated.pkl (deflated 70%)


In [ ]:
product_df = cb_df[['product_id','category_code', 'brand', 'bins']].drop_duplicates()
product_df['price'] = product_df['bins'].apply(lambda x: x.mid)
product_df['product_name'] = product_df.apply(lambda row: row.brand + ' ' + row.category_code.split('.')[-1], axis=1)
product_df.drop(columns = ['brand','bins'], inplace=True)
print(len(product_df))
display(product_df.head())
# print(product_df[product_df['product_id'].isin(g[g['count'] > 1]['product_id'])])
# product_df.drop([16449, 28232629, 28748237, 30079428, 38572337], inplace=True)


27000


product_id                        category_code   price       product_name
1        2735  appliances.environment.water_heater    35.0  aqua water_heater
3       13815                   computers.notebook   255.0    lenovo notebook
4       21204               electronics.smartphone  1085.0   apple smartphone
5       13010                    computers.desktop   905.0     pulser desktop
8        1066                   apparel.shoes.keds   105.0         baden keds

In [ ]:
product_df.to_pickel('products.pkl')

In [ ]:
print(product_df.product_id.nunique())

In [ ]:
events_df = pd.read_pickle('cust_events.pkl')
events_df = events_df[events_df.product_1 != '']
print(events_df.relation.value_counts())

co_view        3495638
co_purchase     169325
p_after_v       149057
Name: relation, dtype: int64


In [ ]:
create_node = """
CREATE (product:product {e_name : $e_name, e_type : $e_type, name : $name, type : $p_type, price : $price, id : $id})
"""

Encoding for product name and product type

In [ ]:
products = product_df.copy()

In [ ]:
products =  pd.read_pickle('products.pkl')
products.head()

product_id                        category_code   price       product_name
1        2735  appliances.environment.water_heater    35.0  aqua water_heater
3       13815                   computers.notebook   255.0    lenovo notebook
4       21204               electronics.smartphone  1085.0   apple smartphone
5       13010                    computers.desktop   905.0     pulser desktop
8        1066                   apparel.shoes.keds   105.0         baden keds

In [ ]:
products['category_code'] = products.category_code.transform(lambda x: x.str.replace('.', ' '))
products['category_code'] = products.category_code.transform(lambda x: x.str.replace('_', ' '))
products['product_name'] = products.product_name.transform(lambda x: x.str.replace('_',' '))
display(products.head())

/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:1: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  """Entry point for launching an IPython kernel.


product_id                        category_code   price       product_name
1        2735  appliances environment water heater    35.0  aqua water heater
3       13815                   computers notebook   255.0    lenovo notebook
4       21204               electronics smartphone  1085.0   apple smartphone
5       13010                    computers desktop   905.0     pulser desktop
8        1066                   apparel shoes keds   105.0         baden keds

In [ ]:
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences

type_tokenizer = Tokenizer()
p_types = products["category_code"].str.split(' ').tolist()
max_length = len(max(p_types, key=len))
type_words = set().union(*p_types)
type_tokenizer.fit_on_texts(type_words)

encoded_types = type_tokenizer.texts_to_sequences(products['category_code'].values.tolist())
padded_types= pad_sequences(encoded_types, maxlen=max_length, padding='post')
products['encoded_type'] = padded_types.tolist()


name_tokenizer = Tokenizer()
p_names = products["product_name"].str.split(' ').tolist()
name_max_length = len(max(p_names, key=len))
name_words = set().union(*p_names)
name_tokenizer.fit_on_texts(name_words)

encoded_names = name_tokenizer.texts_to_sequences(products['product_name'].values.tolist())
padded_names= pad_sequences(encoded_names, maxlen=name_max_length, padding='post')

products['encoded_name'] = padded_names.tolist()
display(products.head())

product_id                        category_code   price       product_name  \
1        2735  appliances environment water heater    35.0  aqua water heater   
3       13815                   computers notebook   255.0    lenovo notebook   
4       21204               electronics smartphone  1085.0   apple smartphone   
5       13010                    computers desktop   905.0     pulser desktop   
8        1066                   apparel shoes keds   105.0         baden keds   

            encoded_type       encoded_name  
1  [1, 116, 152, 164, 0]  [1545, 1029, 260]  
3     [53, 104, 0, 0, 0]     [711, 1651, 0]  
4    [140, 108, 0, 0, 0]     [971, 1734, 0]  
5      [53, 46, 0, 0, 0]      [406, 386, 0]  
8     [163, 6, 30, 0, 0]    [1739, 1379, 0]

In [ ]:
for row in products.itertuples():
    lst = {'e_name': row.encoded_name, 'e_type': row.encoded_type, 'name' : row.product_name, 'p_type' : row.category_code, 'price' : row.price, 'id' : row.product_id}
    session.run(create_node, lst)

In [ ]:
query_1 = """
MATCH (A:product{id:$id1})
MATCH (B:product{id:$id2})
MERGE (A)-[:co_purchase{count:$count}]-(B) 

"""

query_2 = """
MATCH (A:product{id:$id1})
MATCH (B:product{id:$id2})
MERGE (A)-[:similar]-(B) 

"""

In [ ]:
co_viewed = events_df[events_df['relation']=='co_view']
co_purchased = events_df[events_df['relation']=='co_purchase']        
pav = events_df[events_df['relation']=='p_after_v']   

In [ ]:
co_viewed = co_viewed.drop_duplicates()
pav = pav.drop_duplicates()

In [ ]:
print(co_purchased.shape)
cp = co_purchased.copy()
cp = cp.drop_duplicates()
print(cp.shape)

(169325, 3)
(63721, 3)


In [ ]:
similar = pav.copy()
similar['relation'] = 'similar'
print(similar.shape)

#remove product pairs that are purchased together from similar group
cp['relation'] = 'similar'
similar = pd.merge(similar,cp,indicator=True, how= 'left', on =['product_1', 'product_2','relation']).query('_merge=="left_only"').drop(['_merge'], axis=1)
print(similar.shape)

(149057, 3)
(103895, 3)


In [ ]:
display(similar.head())

product_1 product_2 relation
2      22329     21403  similar
3       6025      6155  similar
5      18687     22851  similar
13      8947     21187  similar
15     23823     23822  similar

In [ ]:
display(products[products.product_id.isin([6025,6155])])

product_id                 category_code price        product_name  \
7721            6155  appliances kitchen microwave  75.0  horizont microwave   
40867881        6025  appliances kitchen microwave  65.0       arg microwave   

                encoded_type     encoded_name  
7721      [1, 145, 21, 0, 0]   [755, 1256, 0]  
40867881  [1, 145, 21, 0, 0]  [1068, 1256, 0]

In [ ]:
cop = co_purchased.groupby(['product_1','product_2'])['relation'].count().reset_index(name='count')
print(cop.shape)
display(cop.head())
print(type(cop))

(63721, 3)


product_1  product_2  count
0          2      13521      1
1          2      15022      1
2          3        367      1
3          4         76      2
4          4      15109      1

<class 'pandas.core.frame.DataFrame'>


In [ ]:
for row in cop.itertuples():
    lst = {'id1': row.product_1, 'id2': row.product_2, 'count' : row.count}
    session.run(query_1, lst)
    
# created 61433 co purchase relations in both directions(122866)

In [ ]:
for row in similar.itertuples():
    lst = {'id1': row.product_1, 'id2': row.product_2}
    session.run(query_2, lst)
    
 # created 94944 similar relations in both directions(189888 )

Graphsage training for similar products

In [ ]:
!pip install stellargraph

In [ ]:
import stellargraph as sg
import pandas as pd
import numpy as np
import random

from stellargraph.connector.neo4j import Neo4jGraphSAGENodeGenerator, Neo4jStellarGraph
from stellargraph.layer import GraphSAGE

from stellargraph.mapper import GraphSAGELinkGenerator
from stellargraph.mapper import GraphSAGENodeGenerator
from stellargraph.layer import GraphSAGE, link_classification
from stellargraph.data import UniformRandomWalk
from stellargraph.data import UnsupervisedSampler

In [ ]:
import py2neo
import os

default_host = os.environ.get("STELLARGRAPH_NEO4J_HOST")

# Create the Neo4j Graph database object; the arguments can be edited to specify location and authentication
neo4j_graphdb = py2neo.Graph(host=default_host, port=7687, user='neo4j', password='neo3j')

In [ ]:
print(len(neo4j_graphdb.nodes))

27000


In [ ]:
similar_nodes = neo4j_graphdb.run(
    """
    MATCH (n)-[:similar]-()
    RETURN n.id as id, n.e_name as e_name, n.e_type as e_type, n.price as price
    """
).to_data_frame()
display(similar_nodes.head())
display(similar_nodes.id.nunique())
print(len(similar_nodes))
edges = neo4j_graphdb.run(
    """
    MATCH (n)-[:similar]-(m)
    RETURN n.id AS source, m.id AS target
    """
).to_data_frame()
display(edges.head())

id            e_name                  e_type  price
0  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0
1  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0
2  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0
3  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0
4  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0

15198

189888


source  target
0    2735    5879
1    2735    2906
2    2735     823
3    2735    8930
4    2735   18750

In [ ]:
names= pd.DataFrame(similar_nodes['e_name'].to_list(), columns = ['n1', 'n2', 'n3'])
types = pd.DataFrame(similar_nodes['e_type'].to_list(), columns = ['t1', 't2', 't3','t4','t5'])
result = pd.concat([names, types], axis=1)
result = pd.concat([similar_nodes[['id','price']], result], axis=1)
result.drop_duplicates(inplace=True)
display(similar_nodes.head())
result = result.set_index('id')
display(result)

id            e_name                  e_type  price
0  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0
1  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0
2  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0
3  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0
4  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0

price    n1    n2   n3   t1   t2   t3   t4  t5
id                                                    
2735     35.0  1096   621  763  132   89  111  160   0
13815   255.0   475   882    0   23   16    0    0   0
21204  1085.0   969  1725    0  108   45    0    0   0
13010   905.0   184  1521    0   23   87    0    0   0
1066    105.0   678  1445    0   18   20  152    0   0
...       ...   ...   ...  ...  ...  ...  ...  ...  ..
26877   245.0   982   457    0  101   17    0    0   0
14550   915.0   229   103    0   23  154  118    0   0
14144   195.0   969   767    0   23  154  163    0   0
12756   345.0   475  1521    0   23   87    0    0   0
13379  2325.0   969   882    0   23   16    0    0   0

[15198 rows x 9 columns]

In [ ]:
from stellargraph import StellarGraph
datagraph = StellarGraph( {"product": result},{"similar" :edges})
print(datagraph.info())

StellarGraph: Undirected multigraph
 Nodes: 15198, Edges: 189888

 Node types:
  product: [15198]
    Features: float32 vector, length 9
    Edge types: product-similar->product

 Edge types:
    product-similar->product: [189888]
        Weights: all 1 (default)
        Features: none


In [ ]:
nodes = list(datagraph.nodes())
number_of_walks = 5
length = 2
batch_size = 6
epochs = 40
num_samples = [5, 4]

unsupervised_samples = UnsupervisedSampler(datagraph, nodes=nodes, length=length, number_of_walks=number_of_walks)
generator = GraphSAGELinkGenerator(datagraph, batch_size, num_samples)
train_gen = generator.flow(unsupervised_samples)

layer_sizes = [40, 40]            #determine the size of layers and hence output vectors
graphsage = GraphSAGE(layer_sizes=layer_sizes, generator=generator, bias=True, dropout=0.0, normalize="l2")

# Build the model and expose input and output sockets of graphsage, for node pair inputs:
x_inp, x_out = graphsage.in_out_tensors()
prediction = link_classification(output_dim=1, output_act="sigmoid", edge_embedding_method="ip")(x_out)

link_classification: using 'ip' method to combine node embeddings into edge embeddings


In [ ]:
import tensorflow as tf
graphsage_model = tf.keras.Model(inputs=x_inp, outputs=prediction)

graphsage_model.compile(
    optimizer=tf.keras.optimizers.Adam(learning_rate=1e-2),
    loss=tf.keras.losses.binary_crossentropy,
    metrics=[tf.keras.metrics.binary_accuracy],
)

history = graphsage_model.fit(
    train_gen,
    epochs=epochs,
    verbose=1,
    use_multiprocessing=False,
    workers=4,
    shuffle=True,
)

Epoch 1/40
25330/25330 [==============================] - 123s 5ms/step - loss: 0.5659 - binary_accuracy: 0.7281
Epoch 2/40
25330/25330 [==============================] - 116s 5ms/step - loss: 0.5544 - binary_accuracy: 0.7374
Epoch 3/40
25330/25330 [==============================] - 115s 5ms/step - loss: 0.5510 - binary_accuracy: 0.7395
Epoch 4/40
25330/25330 [==============================] - 116s 5ms/step - loss: 0.5490 - binary_accuracy: 0.7449
Epoch 5/40
25330/25330 [==============================] - 116s 5ms/step - loss: 0.5484 - binary_accuracy: 0.7479
Epoch 6/40
25330/25330 [==============================] - 114s 5ms/step - loss: 0.5474 - binary_accuracy: 0.7525
Epoch 7/40
25330/25330 [==============================] - 114s 4ms/step - loss: 0.5475 - binary_accuracy: 0.7516
Epoch 8/40
25330/25330 [==============================] - 113s 4ms/step - loss: 0.5470 - binary_accuracy: 0.7546
Epoch 9/40
25330/25330 [==============================] - 112s 4ms/step - loss: 0.5457 - binary_

Extracting node embeddings

In [ ]:
x_inp_src = x_inp[0::2]
x_out_src = x_out[0]
embedding_model = tf.keras.Model(inputs=x_inp_src, outputs=x_out_src)

In [ ]:
node_list = result.index
final_products = products[products['product_id'].isin(node_list)]
node_ids = final_products.product_id.values.tolist()
node_gen = GraphSAGENodeGenerator(datagraph, batch_size, num_samples).flow(node_ids)
node_embeddings = embedding_model.predict(node_gen, workers=4, verbose=1)

2533/2533 [==============================] - 8s 3ms/step


In [ ]:
print(node_embeddings[0])

[-0.09308784 -0.00837598 -0.36120594 -0.07669535 -0.22251074 -0.01539307
 -0.08419011 -0.2822534  -0.41815788  0.33040124 -0.4319311  -0.3506831
 -0.0839932  -0.2388001  -0.08158364  0.04319631  0.13280062 -0.10456815
 -0.09824365  0.00572406  0.01218955 -0.00439755 -0.04797333  0.00198377
  0.03055515  0.00245371 -0.04892607 -0.03299997  0.05391613 -0.02395441
  0.00285639  0.02671103  0.01681678 -0.0011026   0.04288871 -0.00148707
  0.02672692  0.00316672 -0.00579367  0.00259361]


In [ ]:
type(node_embeddings)

numpy.ndarray

In [ ]:
embedding_model.save('embedding_model.h5')

In [ ]:
final_products.loc[:,'embedding'] = node_embeddings.tolist()
final_products.head()

/opt/conda/lib/python3.7/site-packages/pandas/core/indexing.py:1667: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[key] = value


product_id                        category_code   price       product_name  \
1        2735  appliances environment water heater    35.0  aqua water heater   
3       13815                   computers notebook   255.0    lenovo notebook   
4       21204               electronics smartphone  1085.0   apple smartphone   
5       13010                    computers desktop   905.0     pulser desktop   
8        1066                   apparel shoes keds   105.0         baden keds   

            encoded_type       encoded_name  \
1  [1, 116, 152, 164, 0]  [1545, 1029, 260]   
3     [53, 104, 0, 0, 0]     [711, 1651, 0]   
4    [140, 108, 0, 0, 0]     [971, 1734, 0]   
5      [53, 46, 0, 0, 0]      [406, 386, 0]   
8     [163, 6, 30, 0, 0]    [1739, 1379, 0]   

                                           embedding  
1  [-0.09308783710002899, -0.008375982753932476, ...  
3  [-0.04514121264219284, -0.2976009249687195, 0....  
4  [-0.09630400687456131, 0.02939446270465851, 0....  
5  [-0.012490401975810528, -0.4181481897830963, 0...  
8  [0.12861299514770508, -0.22676336765289307, 0....

In [ ]:
X = final_products.copy()

In [ ]:
from sklearn.manifold import TSNE
import numpy as np
import altair as alt
X_embedded = TSNE(n_components=2, n_jobs =-1).fit_transform(list(X.embedding))

/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:783: FutureWarning: The default initialization in TSNE will change from 'random' to 'pca' in 1.2.
  FutureWarning,
/opt/conda/lib/python3.7/site-packages/sklearn/manifold/_t_sne.py:793: FutureWarning: The default learning rate in TSNE will change from 200.0 to 'auto' in 1.2.
  FutureWarning,


In [ ]:
products_display = str(X.product_name)
df = pd.DataFrame(data = {
    "product": products_display,
    "type" : X.category_code,
    "x": [value[0] for value in X_embedded],
    "y": [value[1] for value in X_embedded]
})

alt.data_transformers.enable('default', max_rows=None)
alt.Chart(df).mark_circle(size=60).encode(
    x='x',
    y='y',
    color='type',
    tooltip=['product', 'type']
).properties(width=700, height=400)

alt.Chart(...)

In [ ]:
final_products['embedding'] = final_products['embedding'].apply(lambda x: np.array(x))


/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [ ]:
final_products.head()

product_id                        category_code   price       product_name  \
1        2735  appliances environment water heater    35.0  aqua water heater   
3       13815                   computers notebook   255.0    lenovo notebook   
4       21204               electronics smartphone  1085.0   apple smartphone   
5       13010                    computers desktop   905.0     pulser desktop   
8        1066                   apparel shoes keds   105.0         baden keds   

            encoded_type       encoded_name  \
1  [1, 116, 152, 164, 0]  [1545, 1029, 260]   
3     [53, 104, 0, 0, 0]     [711, 1651, 0]   
4    [140, 108, 0, 0, 0]     [971, 1734, 0]   
5      [53, 46, 0, 0, 0]      [406, 386, 0]   
8     [163, 6, 30, 0, 0]    [1739, 1379, 0]   

                                           embedding  
1  [-0.09308783710002899, -0.008375982753932476, ...  
3  [-0.04514121264219284, -0.2976009249687195, 0....  
4  [-0.09630400687456131, 0.02939446270465851, 0....  
5  [-0.012490401975810528, -0.4181481897830963, 0...  
8  [0.12861299514770508, -0.22676336765289307, 0....

In [ ]:
from sklearn.metrics.pairwise import cosine_similarity
q = 9562     # janome sewing machine
b = [19467,9645,8929,11417] #'kenwood subwoofer','leader sewing machine','samsung washer','asrock motherboard'

a = final_products[final_products.product_id == q]
a_name = a.product_name
x=a.embedding.tolist()
for each in b:
    pos = final_products[final_products.product_id == each]
    y=pos.embedding.tolist()
    y_name = pos.product_name
    print(abs(cosine_similarity(x[0].reshape(1,-1),y[0].reshape(1,-1))),a_name,"<----->" ,y_name)

[[0.00323299]] 657    janome sewing machine
Name: product_name, dtype: object <-----> 49072603    kenwood subwoofer
Name: product_name, dtype: object
[[0.89820941]] 657    janome sewing machine
Name: product_name, dtype: object <-----> 38234    leader sewing machine
Name: product_name, dtype: object
[[0.03166474]] 657    janome sewing machine
Name: product_name, dtype: object <-----> 646    samsung washer
Name: product_name, dtype: object
[[0.33517479]] 657    janome sewing machine
Name: product_name, dtype: object <-----> 2776    asrock motherboard
Name: product_name, dtype: object


Generating embeddings for all nodes uisng the trained Graphsage model

In [ ]:
#getting embeddings for all nodes
from stellargraph import StellarGraph
all_nodes = neo4j_graphdb.run(
    """
    MATCH (n)-[]-()
    RETURN n.id as id, n.e_name as e_name, n.e_type as e_type, n.price as price
    """
).to_data_frame()
display(all_nodes.head())
display(all_nodes.id.nunique())
print(len(all_nodes))
all_edges = neo4j_graphdb.run(
    """
    MATCH (n)-[]-(m)
    RETURN n.id AS source, m.id AS target
    """
).to_data_frame()
display(all_edges.head())

names= pd.DataFrame(all_nodes['e_name'].to_list(), columns = ['n1', 'n2', 'n3'])
types = pd.DataFrame(all_nodes['e_type'].to_list(), columns = ['t1', 't2', 't3','t4','t5'])
all_result = pd.concat([names, types], axis=1)
all_result = pd.concat([all_nodes[['id','price']], all_result], axis=1)
all_result.drop_duplicates(inplace=True)
display(all_nodes.head())
all_result = all_result.set_index('id')
display(all_result)

full_graph = StellarGraph( {"product": all_result},{"relation" :all_edges})
print(full_graph.info())

id            e_name                  e_type  price
0  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0
1  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0
2  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0
3  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0
4  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0

15580

312754


source  target
0    2735     896
1    2735    1839
2    2735    1901
3    2735    2156
4    2735    2528

id            e_name                  e_type  price
0  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0
1  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0
2  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0
3  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0
4  2735  [1096, 621, 763]  [132, 89, 111, 160, 0]   35.0

price    n1    n2   n3   t1   t2   t3   t4  t5
id                                                    
2735     35.0  1096   621  763  132   89  111  160   0
13815   255.0   475   882    0   23   16    0    0   0
21204  1085.0   969  1725    0  108   45    0    0   0
13010   905.0   184  1521    0   23   87    0    0   0
1066    105.0   678  1445    0   18   20  152    0   0
...       ...   ...   ...  ...  ...  ...  ...  ...  ..
14550   915.0   229   103    0   23  154  118    0   0
14144   195.0   969   767    0   23  154  163    0   0
12756   345.0   475  1521    0   23   87    0    0   0
13301   995.0   969   882    0   23   16    0    0   0
13379  2325.0   969   882    0   23   16    0    0   0

[15580 rows x 9 columns]

StellarGraph: Undirected multigraph
 Nodes: 15580, Edges: 312754

 Node types:
  product: [15580]
    Features: float32 vector, length 9
    Edge types: product-relation->product

 Edge types:
    product-relation->product: [312754]
        Weights: all 1 (default)
        Features: none


In [ ]:
batch_size = 6
num_samples = [5, 4]

print(len(final_products))
node_list = all_result.index
final_products = products[products['product_id'].isin(node_list)]
node_ids = final_products.product_id.values.tolist()
node_gen = GraphSAGENodeGenerator(full_graph, batch_size, num_samples).flow(node_ids)
all_node_embeddings = embedding_model.predict(node_gen, workers=4, verbose=1)
print(len(final_products))

15198
2597/2597 [==============================] - 10s 4ms/step
15580


In [ ]:
final_products.loc[:,'embedding'] = all_node_embeddings.tolist()
final_products['embedding'] = final_products['embedding'].apply(lambda x: np.array(x))

/opt/conda/lib/python3.7/site-packages/pandas/core/indexing.py:1667: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[key] = value
/opt/conda/lib/python3.7/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [ ]:
from sklearn.metrics.pairwise import cosine_similarity
q = 9562     # janome sewing machine
b = [19467,9645,8929,11417] #'kenwood subwoofer','leader sewing machine','samsung washer','asrock motherboard'

a = final_products[final_products.product_id == q]
a_name = a.product_name
x=a.embedding.tolist()
for each in b:
    pos = final_products[final_products.product_id == each]
    y=pos.embedding.tolist()
    y_name = pos.product_name
    print(abs(cosine_similarity(x[0].reshape(1,-1),y[0].reshape(1,-1))),a_name,"<----->" ,y_name)

[[0.07470097]] 657    janome sewing machine
Name: product_name, dtype: object <-----> 49072603    kenwood subwoofer
Name: product_name, dtype: object
[[0.91170841]] 657    janome sewing machine
Name: product_name, dtype: object <-----> 38234    leader sewing machine
Name: product_name, dtype: object
[[0.10497977]] 657    janome sewing machine
Name: product_name, dtype: object <-----> 646    samsung washer
Name: product_name, dtype: object
[[0.24540471]] 657    janome sewing machine
Name: product_name, dtype: object <-----> 2776    asrock motherboard
Name: product_name, dtype: object


In [ ]:
# fp_copy = final_products.copy()
final_products.to_pickle('final_products.pkl')# saved embeddings with 40 epoch

type transition training

In [ ]:
# comp = pd.read_csv('sample_co_purchase.csv')
# print(comp['complementary'][0])
# print(type(comp['complementary'][0]))
# comp.loc[:,'complementary'] = comp.loc[:,'complementary'].apply(lambda x: x.strip('[,]').split(', '))
# print(comp['complementary'][0])
# print(type(comp['complementary'][0]))
# display(comp.head())

In [ ]:
categories = list(set(final_products.category_code.values.tolist()))
print(len(categories))

df = pd.merge(left=cop, right=products, how='left', left_on='product_1', right_on='product_id')
print(len(df))
df.drop(columns =['product_id'], inplace=True)
df.rename(columns={'category_code' : 'p1_type'}, inplace=True)
df = pd.merge(left=df, right=products, how='left', left_on='product_2', right_on='product_id')
df.drop(columns =['product_id'], inplace=True)
df.rename(columns={'category_code' : 'p2_type'}, inplace=True)
df = df[['product_1','product_2','p1_type','p2_type','count']]
display(df.head())
print(df.p1_type.nunique())

124
63721


product_1  product_2          p1_type                      p2_type  count
0          2      13521  accessories bag           computers notebook      1
1          2      15022  accessories bag  computers peripherals mouse      1
2          3        367  accessories bag              accessories bag      1
3          4         76  accessories bag              accessories bag      2
4          4      15109  accessories bag  computers peripherals mouse      1

116


In [ ]:
category = 'electronics audio subwoofer'
cnew = df[(df.p1_type== category) & (df['count'] >0) & (df.p1_type != df.p2_type)]
cnew = cnew[cnew.p2_type != 'electronics smartphone']
cnew = cnew.groupby(['p1_type','p2_type'])['p2_type'].count().reset_index(name='count_2')
# cnew = cnew.groupby(['p1_type','p2_type'])['p2_type'].count().reset_index(name='count_2')
cnew = cnew.sort_values(by=['count_2'], ascending=False).head(3)
if len(cnew) > 0:
    lst = {'query' : category, 'complementary' : cnew.p2_type.values.tolist()}
print(lst)    
display(cnew)

{'query': 'electronics audio subwoofer', 'complementary': ['auto accessories player', 'electronics audio headphone', 'auto accessories alarm']}


p1_type                      p2_type  count_2
20  electronics audio subwoofer      auto accessories player       55
28  electronics audio subwoofer  electronics audio headphone       14
19  electronics audio subwoofer       auto accessories alarm       10

In [ ]:
comp =  pd.DataFrame(columns = ['query', 'complementary'])

In [ ]:
# prepared_categories = comp['query'].values.tolist()
prepared_categories =[]
new_cats = []
for category in categories:
    if category not in prepared_categories:
        cnew = df[(df.p1_type==category) & (df['count'] >0) & (df.p1_type != df.p2_type)]
        cnew = cnew[cnew.p2_type != 'electronics smartphone']
        cnew = cnew.groupby(['p1_type','p2_type'])['p2_type'].count().reset_index(name='count_2')
        # display(category,cnew.groupby(['p1_type','p2_type'])['p2_type'].count().reset_index(name='count_2'))
        cnew = cnew.sort_values(by=['count_2'], ascending=False).head(3)
        if len(cnew) > 0:
            lst = {'query' : category, 'complementary' : cnew.p2_type.values.tolist()}
            new_cats.append(lst)
            

print(len(comp))
comp = comp.append(new_cats, ignore_index=True, sort=False)
print(len(comp))

0
113


In [ ]:
display(comp)

query  \
0      appliances kitchen kettle   
1         construction tools saw   
2      appliances sewing machine   
3        apparel shoes moccasins   
4                  apparel dress   
..                           ...   
108            apparel underwear   
109    appliances kitchen toster   
110    appliances kitchen washer   
111                  kids skates   
112  auto accessories compressor   

                                         complementary  
0    [appliances iron, appliances environment vacuu...  
1    [construction tools drill, appliances kitchen ...  
2    [appliances environment vacuum, appliances iro...  
3    [apparel shoes, apparel shoes keds, auto acces...  
4       [apparel jumper, apparel shirt, apparel shoes]  
..                                                 ...  
108  [electronics video tv, appliances kitchen mixe...  
109  [electronics audio headphone, appliances kitch...  
110  [electronics video tv, appliances kitchen refr...  
111  [electronics clocks, electronics audio headpho...  
112  [construction tools painting, electronics audi...  

[113 rows x 2 columns]

In [ ]:
terms = tf.ragged.constant(list(set(products.category_code.values.tolist())))
lookup = tf.keras.layers.StringLookup(output_mode="multi_hot")
lookup.adapt(terms)
vocab = lookup.get_vocabulary()


def invert_multi_hot(encoded_labels):
    """Reverse a single multi-hot encoded label to a tuple of vocab terms."""
    hot_indices = np.argwhere(encoded_labels == 1.0)[..., 0]
    return np.take(vocab, hot_indices)


print("Vocabulary:\n")
print(vocab)
print(len(vocab))

Vocabulary:

['[UNK]', 'stationery cartrige', 'sport trainer', 'sport tennis', 'sport snowboard', 'sport ski', 'sport bicycle', 'medicine tools tonometer', 'kids toys', 'kids swing', 'kids skates', 'kids fmcg diapers', 'kids dolls', 'kids carriage', 'furniture universal light', 'furniture living room sofa', 'furniture living room chair', 'furniture living room cabinet', 'furniture kitchen table', 'furniture kitchen chair', 'furniture bedroom pillow', 'furniture bedroom blanket', 'furniture bedroom bed', 'furniture bathroom toilet', 'furniture bathroom bath', 'electronics video tv', 'electronics video projector', 'electronics telephone', 'electronics tablet', 'electronics smartphone', 'electronics clocks', 'electronics camera video', 'electronics camera photo', 'electronics audio subwoofer', 'electronics audio music tools piano', 'electronics audio microphone', 'electronics audio headphone', 'electronics audio acoustic', 'country yard lawn mower', 'country yard furniture hammok', 'count

In [ ]:
encoded = lookup(['appliances environment water heater', 'appliances kitchen refrigerators', 'appliances kitchen oven'])
print(encoded)
cats = invert_multi_hot(encoded)
print(cats)

tf.Tensor(
[0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.
 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.], shape=(130,), dtype=float32)
['appliances kitchen refrigerators' 'appliances kitchen oven'
 'appliances environment water heater']


In [ ]:
comp.loc[:,'label'] = comp.apply(lambda x: lookup(x['complementary']),axis=1)
display(comp.head())
print(comp['complementary'][0])

encoded = comp['label'][0]
cats = invert_multi_hot(encoded)
print(cats)

query  \
0  appliances kitchen kettle   
1     construction tools saw   
2  appliances sewing machine   
3    apparel shoes moccasins   
4              apparel dress   

                                       complementary  \
0  [appliances iron, appliances environment vacuu...   
1  [construction tools drill, appliances kitchen ...   
2  [appliances environment vacuum, appliances iro...   
3  [apparel shoes, apparel shoes keds, auto acces...   
4     [apparel jumper, apparel shirt, apparel shoes]   

                                               label  
0  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...  
1  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...  
2  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...  
3  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...  
4  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...

['appliances iron', 'appliances environment vacuum', 'appliances kitchen microwave']
['appliances kitchen microwave' 'appliances iron'
 'appliances environment vacuum']


In [ ]:
final_df = pd.merge(left=final_products, right=comp, how='left', left_on='category_code', right_on='query')
print(len(final_df))
# test = final_df[final_df.isna().any(axis=1)]
# display(test)
# t_list= list(set(test.category_code.values.tolist()))
# print(t_list)
# display(df[(df.p1_type.isin(t_list)) | (df.p1_type.isin(t_list))])
final_df = final_df.dropna()
print(len(final_df))
final_df = final_df[final_df['query'].map(final_df['query'].value_counts()) > 1]
print(len(final_df))
display(final_df.head())

15580
15512
15512


product_id                        category_code   price       product_name  \
0        2735  appliances environment water heater    35.0  aqua water heater   
1       13815                   computers notebook   255.0    lenovo notebook   
2       21204               electronics smartphone  1085.0   apple smartphone   
3       13010                    computers desktop   905.0     pulser desktop   
4        1066                   apparel shoes keds   105.0         baden keds   

            encoded_type       encoded_name  \
0  [1, 116, 152, 164, 0]  [1545, 1029, 260]   
1     [53, 104, 0, 0, 0]     [711, 1651, 0]   
2    [140, 108, 0, 0, 0]     [971, 1734, 0]   
3      [53, 46, 0, 0, 0]      [406, 386, 0]   
4     [163, 6, 30, 0, 0]    [1739, 1379, 0]   

                                           embedding  \
0  [-0.025843141600489616, -0.08541616797447205, ...   
1  [-0.1369248777627945, -0.062374379485845566, 0...   
2  [-0.0843409076333046, -0.056637875735759735, 0...   
3  [-0.055632177740335464, -0.44864213466644287, ...   
4  [0.08506312966346741, -0.26524463295936584, 0....   

                                 query  \
0  appliances environment water heater   
1                   computers notebook   
2               electronics smartphone   
3                    computers desktop   
4                   apparel shoes keds   

                                       complementary  \
0  [appliances kitchen washer, appliances environ...   
1  [electronics audio headphone, electronics vide...   
2  [electronics audio headphone, electronics cloc...   
3  [computers peripherals monitor, computers note...   
4  [apparel shoes, electronics clocks, electronic...   

                                               label  
0  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...  
1  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...  
2  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...  
3  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...  
4  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...

In [ ]:
from sklearn.model_selection import train_test_split
type_train_df, type_test_df = train_test_split(
    final_df,
    test_size=0.1,
    random_state=16,
    stratify=final_df['label'].values.tolist(),
)

In [ ]:
type_train_df = type_train_df[['product_id', 'product_name' , 'embedding', 'query', 'complementary', 'label']]
display(type_train_df.head())

product_id           product_name  \
15009       24209  lorelli-bertoni chair   
11546       21599        oppo smartphone   
10569       21139       apple smartphone   
13862       12382          apple desktop   
3077        22928                  lg tv   

                                               embedding  \
15009  [-0.12708047032356262, 0.08347580581903458, -0...   
11546  [-0.14800682663917542, 0.08963550627231598, 0....   
10569  [-0.13008493185043335, 0.0725097730755806, 0.0...   
13862  [0.016921263188123703, -0.4080825448036194, 0....   
3077   [-0.1062176376581192, -0.24529710412025452, -0...   

                         query  \
15009  furniture kitchen chair   
11546   electronics smartphone   
10569   electronics smartphone   
13862        computers desktop   
3077      electronics video tv   

                                           complementary  \
15009  [furniture kitchen table, furniture living roo...   
11546  [electronics audio headphone, electronics cloc...   
10569  [electronics audio headphone, electronics cloc...   
13862  [computers peripherals monitor, computers note...   
3077   [appliances kitchen washer, appliances environ...   

                                                   label  
15009  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...  
11546  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...  
10569  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...  
13862  (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...  
3077   (tf.Tensor(0.0, shape=(), dtype=float32), tf.T...

In [ ]:
X_train = type_train_df['embedding'].values.tolist()
y_train = type_train_df['label'].values.tolist()
X_train= np.array(X_train).astype(np.float32)
y_train = np.array(y_train).astype(np.float32)

In [ ]:
print(lookup.vocabulary_size())

130


In [ ]:
def make_model():
    shallow_mlp_model = tf.keras.Sequential(
        [
            tf.keras.layers.Dense(
            256, activation="relu", input_shape=(X_train.shape[1],)),
            tf.keras.layers.Dense(512, activation="relu"),
            tf.keras.layers.Dropout(0.3),
            tf.keras.layers.Dense(256, activation="relu"),
            tf.keras.layers.Dropout(0.2),
            tf.keras.layers.Dense(lookup.vocabulary_size(), activation="sigmoid"),
        ] 
    )
    return shallow_mlp_model

In [ ]:
epochs = 50

metrics = [
    # keras.metrics.FalseNegatives(name="fn"),
    # keras.metrics.FalsePositives(name="fp"),
    # keras.metrics.TrueNegatives(name="tn"),
    # keras.metrics.TruePositives(name="tp"),
    tf.keras.metrics.Precision(name="precision"),
    tf.keras.metrics.Recall(name="recall"),
]
shallow_mlp_model = make_model()
shallow_mlp_model.compile(
    loss="binary_crossentropy", optimizer=tf.keras.optimizers.Adam(1e-3), metrics=metrics
)

history = shallow_mlp_model.fit(
    X_train, y_train, batch_size=8, epochs=epochs, validation_split = 0.2
)

Epoch 1/50
1396/1396 [==============================] - 5s 3ms/step - loss: 0.0557 - precision: 0.6314 - recall: 0.3822 - val_loss: 0.0347 - val_precision: 0.8042 - val_recall: 0.5669
Epoch 2/50
1396/1396 [==============================] - 4s 3ms/step - loss: 0.0337 - precision: 0.7941 - recall: 0.6070 - val_loss: 0.0276 - val_precision: 0.8332 - val_recall: 0.6991
Epoch 3/50
1396/1396 [==============================] - 4s 3ms/step - loss: 0.0280 - precision: 0.8284 - recall: 0.6962 - val_loss: 0.0240 - val_precision: 0.8605 - val_recall: 0.7488
Epoch 4/50
1396/1396 [==============================] - 4s 3ms/step - loss: 0.0248 - precision: 0.8454 - recall: 0.7388 - val_loss: 0.0223 - val_precision: 0.8550 - val_recall: 0.7824
Epoch 5/50
1396/1396 [==============================] - 4s 3ms/step - loss: 0.0226 - precision: 0.8558 - recall: 0.7683 - val_loss: 0.0202 - val_precision: 0.8770 - val_recall: 0.7979
Epoch 6/50
1396/1396 [==============================] - 4s 3ms/step - loss: 0.02

In [ ]:

X_test = type_test_df['embedding'].values.tolist()
y_test = type_test_df['label'].values.tolist()
X_test=np.array(X_test).astype(np.float32)
y_test = np.array(y_test).astype(np.float32)
print(y_test.shape)
result = shallow_mlp_model.evaluate(X_test,y_test)

(1552, 130)
49/49 [==============================] - 0s 3ms/step - loss: 0.0172 - precision: 0.9056 - recall: 0.8863


In [ ]:
shallow_mlp_model.save('shallow_mlp_model.h5')

In [ ]:
sample = X_test[:10]
product_names = type_test_df['product_name'].values.tolist()[:10]
predicted_probabilities = shallow_mlp_model.predict(sample)

In [ ]:
for i in range(10):
    predicted_proba = [proba for proba in predicted_probabilities[i]]
    top_3_labels = [
        x
        for _, x in sorted(
            zip(predicted_probabilities[i], lookup.get_vocabulary()),
            key=lambda pair: pair[0],
            reverse=True,
        )
    ][:3]
    print(f"Recommended Types for "+product_names[i]+ " are : ")
    print(f"Predicted Label(s): ({', '.join([label for label in top_3_labels])})")
    print(f"Actual Label(s):  ({', '.join([label for label in invert_multi_hot(y_test[i])])})")
    print(" ")

Recommended Types for samsung vacuum are : 
Predicted Label(s): (appliances kitchen microwave, appliances iron, electronics video tv)
Actual Label(s):  (electronics video tv, appliances kitchen microwave, appliances iron)
 
Recommended Types for atlant refrigerators are : 
Predicted Label(s): (appliances environment vacuum, electronics video tv, appliances kitchen washer)
Actual Label(s):  (electronics video tv, appliances kitchen washer, appliances environment vacuum)
 
Recommended Types for doogee smartphone are : 
Predicted Label(s): (electronics video tv, electronics audio headphone, electronics clocks)
Actual Label(s):  (electronics video tv, electronics clocks, electronics audio headphone)
 
Recommended Types for willmark air heater are : 
Predicted Label(s): (electronics video tv, appliances environment water heater, appliances kitchen kettle)
Actual Label(s):  (electronics video tv, appliances kitchen kettle, appliances environment water heater)
 
Recommended Types for intel cp

item prediction

NN based prediction

In [ ]:
shallow_mlp_model = tf.keras.models.load_model('shallow_mlp_model.h5')

In [ ]:
df = pd.merge(left=cop, right=products, how='left', left_on='product_1', right_on='product_id')
# df = df[~df['category_code'].isin(['electronics smartphone','electronics tablet', 'computers notebook','computers desktop'])]
df.drop(columns =['product_id'], inplace=True)
df.rename(columns={'category_code' : 'p1_type'}, inplace=True)
df = pd.merge(left=df, right=products, how='left', left_on='product_2', right_on='product_id')
df.drop(columns =['product_id'], inplace=True)
df.rename(columns={'category_code' : 'p2_type'}, inplace=True)
df = df[['product_1', 'product_2', 'count', 'product_name_x', 'product_name_y', 'p1_type', 'p2_type']]
display(df.head())


product_1  product_2  count product_name_x     product_name_y  \
0          2      13521      1       acer bag  deepcool notebook   
1          2      15022      1       acer bag       canyon mouse   
2          3        367      1       acer bag         sumdex bag   
3          4         76      2       acer bag      continent bag   
4          4      15109      1       acer bag    microsoft mouse   

           p1_type                      p2_type  
0  accessories bag           computers notebook  
1  accessories bag  computers peripherals mouse  
2  accessories bag              accessories bag  
3  accessories bag              accessories bag  
4  accessories bag  computers peripherals mouse

In [ ]:
print(df.product_1.nunique())

6393


In [ ]:
cop_df= df.groupby(['product_name_x', 'product_name_y','p2_type'])['product_name_y'].count().reset_index(name='purchase_count')

cop_df = cop_df[cop_df.p2_type != 'electronics.smartphone']
display(cop_df.head())


product_name_x     product_name_y                      p2_type  \
0       acer bag       canyon mouse  computers peripherals mouse   
1       acer bag      continent bag              accessories bag   
2       acer bag  deepcool notebook           computers notebook   
3       acer bag    microsoft mouse  computers peripherals mouse   
4       acer bag         sumdex bag              accessories bag   

   purchase_count  
0               1  
1               1  
2               1  
3               1  
4               1

In [ ]:
sub_df = cop_df[cop_df.product_name_x == 'yamaha piano']
display(sub_df)
cnew = sub_df.groupby(['product_name_x','p2_type']).max()
for row in cnew.itertuples():
    ct = getattr(row, 'Index')[1]
    print(ct,row.product_name_y)


product_name_x      product_name_y                              p2_type  \
18285   yamaha piano          akai piano  electronics audio music tools piano   
18286   yamaha piano        apple clocks                   electronics clocks   
18287   yamaha piano    apple smartphone               electronics smartphone   
18288   yamaha piano          braun iron                      appliances iron   
18289   yamaha piano      cortland piano  electronics audio music tools piano   
18290   yamaha piano      indesit washer            appliances kitchen washer   
18291   yamaha piano        nexpero keds                   apparel shoes keds   
18292   yamaha piano        philips iron                      appliances iron   
18293   yamaha piano  samsung smartphone               electronics smartphone   
18294   yamaha piano          samsung tv                 electronics video tv   
18295   yamaha piano        yamaha piano  electronics audio music tools piano   

       purchase_count  
18285               1  
18286               1  
18287               1  
18288               1  
18289               3  
18290               1  
18291               1  
18292               1  
18293               2  
18294               1  
18295               6

apparel shoes keds nexpero keds
appliances iron philips iron
appliances kitchen washer indesit washer
electronics audio music tools piano yamaha piano
electronics clocks apple clocks
electronics smartphone samsung smartphone
electronics video tv samsung tv


In [ ]:
purchases = df[(df.product_name_x == 'yamaha piano') & (df.product_name_y == 'yamaha piano')]
purchases

product_1  product_2  count product_name_x product_name_y  \
26525      19236      19239      1   yamaha piano   yamaha piano   
26532      19239      19236      1   yamaha piano   yamaha piano   
26534      19240      19244      1   yamaha piano   yamaha piano   
26537      19242      19240      1   yamaha piano   yamaha piano   
26541      19244      19240      1   yamaha piano   yamaha piano   
26543      19249      19242      1   yamaha piano   yamaha piano   

                                   p1_type  \
26525  electronics audio music tools piano   
26532  electronics audio music tools piano   
26534  electronics audio music tools piano   
26537  electronics audio music tools piano   
26541  electronics audio music tools piano   
26543  electronics audio music tools piano   

                                   p2_type  
26525  electronics audio music tools piano  
26532  electronics audio music tools piano  
26534  electronics audio music tools piano  
26537  electronics audio music tools piano  
26541  electronics audio music tools piano  
26543  electronics audio music tools piano

In [ ]:
types_df =  pd.DataFrame(columns=['query_product', 'query_embedding', 'comp_type', 'comp_item', 'comp_embedding'])
types =[]
cp_products = cop_df.product_name_x.values.tolist()

In [ ]:
for item in tqdm(cp_products):
    sub_df = cop_df[cop_df.product_name_x == item]
    cnew = sub_df.groupby(['product_name_x','p2_type']).max()
    for row in cnew.itertuples():
        ct = getattr(row, 'Index')[1]
        purchases = df[(df.product_name_x == item) & (df.product_name_y == row.product_name_y)]
        for embed_row in purchases.itertuples():
            q_embed = final_products[final_products['product_id'] == embed_row.product_1]['embedding'].values[0]
            c_embed = final_products[final_products['product_id'] == embed_row.product_2]['embedding'].values[0]
            lst = {'query_product' : item ,'query_embedding' : q_embed, 'comp_type' : ct , 'comp_item' : row.product_name_y, 'comp_embedding' : c_embed}
            types.append(lst) 


 98%|█████████▊| 18011/18462 [1:14:09<05:48,  1.30it/s]  IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [ ]:
types_df = types_df.append(types)            
display(types_df.head())       
encoded_types = type_tokenizer.texts_to_sequences(types_df['comp_type'].values.tolist())
padded_types= pad_sequences(encoded_types, maxlen=max_length, padding='post')
types_df['enc_type'] = padded_types.tolist()

query_product                                    query_embedding  \
0      acer bag  [-0.09161314368247986, 0.2696472108364105, 0.1...   
1      acer bag  [0.1397686004638672, 0.3450341522693634, 0.149...   
2      acer bag  [-0.1375209540128708, 0.33078208565711975, 0.2...   
3      acer bag  [-0.09161314368247986, 0.2696472108364105, 0.1...   
4      acer bag  [0.1397686004638672, 0.3450341522693634, 0.149...   

                     comp_type          comp_item  \
0              accessories bag         sumdex bag   
1           computers notebook  deepcool notebook   
2  computers peripherals mouse    microsoft mouse   
3              accessories bag         sumdex bag   
4           computers notebook  deepcool notebook   

                                      comp_embedding  
0  [-0.0673522800207138, 0.37397855520248413, 0.0...  
1  [-0.06609289348125458, 0.04110018536448479, 0....  
2  [0.2716103196144104, 0.2735309302806854, -0.01...  
3  [-0.0673522800207138, 0.37397855520248413, 0.0...  
4  [-0.06609289348125458, 0.04110018536448479, 0....

In [ ]:
print(types_df['comp_item'].nunique())
types_df = types_df[types_df['comp_item'].map(types_df['comp_embedding'].value_counts()) > 1]
print(types_df['comp_item'].nunique())

In [ ]:
display(types_df.head()) 

query_product                                    query_embedding  \
0      acer bag  [-0.09161314368247986, 0.2696472108364105, 0.1...   
1      acer bag  [0.1397686004638672, 0.3450341522693634, 0.149...   
2      acer bag  [-0.1375209540128708, 0.33078208565711975, 0.2...   
3      acer bag  [-0.09161314368247986, 0.2696472108364105, 0.1...   
4      acer bag  [0.1397686004638672, 0.3450341522693634, 0.149...   

                     comp_type          comp_item  \
0              accessories bag         sumdex bag   
1           computers notebook  deepcool notebook   
2  computers peripherals mouse    microsoft mouse   
3              accessories bag         sumdex bag   
4           computers notebook  deepcool notebook   

                                      comp_embedding            enc_type  
0  [-0.0673522800207138, 0.37397855520248413, 0.0...   [44, 52, 0, 0, 0]  
1  [-0.06609289348125458, 0.04110018536448479, 0....  [53, 104, 0, 0, 0]  
2  [0.2716103196144104, 0.2735309302806854, -0.01...  [53, 60, 81, 0, 0]  
3  [-0.0673522800207138, 0.37397855520248413, 0.0...   [44, 52, 0, 0, 0]  
4  [-0.06609289348125458, 0.04110018536448479, 0....  [53, 104, 0, 0, 0]

In [ ]:
types_df.to_pickle('types_df.pkl')

In [ ]:
from sklearn.model_selection import train_test_split
train_df, test_df = train_test_split(
    types_df,
    test_size=0.2,
    random_state=42
)

In [ ]:
q_embed = train_df['query_embedding'].values.tolist()
q_embed=np.array(q_embed).astype(np.float32)


c_item = train_df['enc_type'].values.tolist()
c_item=np.array(c_item).astype(np.float32)


y_train = train_df['comp_embedding'].values.tolist()
y_train = np.array(y_train).astype(np.float32)

print(y_train.shape)

(1006352, 40)


In [ ]:
vocab_size = len(type_tokenizer.word_index) + 1

from tensorflow.keras import Input
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Dense, Activation, Multiply
from keras.layers.embeddings import Embedding
from keras.layers import Flatten

input_1 = Input(shape=(5,))   
input_2 = Input(shape=(40,)) 
type_embed = Embedding(input_dim=vocab_size,output_dim=8,input_length=max_length, mask_zero=True)(input_1)
type_out = Flatten()(type_embed)
type_out = Dense(256, activation ='sigmoid')(type_out)

query_out = Dense(256, activation ='sigmoid')(input_2)

multiply = Multiply()([query_out, type_out])
dense_final = Dense(256, activation ='relu')(multiply)
out = Dense(40)(dense_final)

# compile
model = Model(inputs=[input_1, input_2], outputs=out)
model.compile(loss=['mse', tf.keras.losses.CosineSimilarity(axis=1)], optimizer='adam', metrics=[tf.keras.metrics.CosineSimilarity(axis=1)])
print(model.summary())

Model: "model_2"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_7 (InputLayer)           [(None, 5)]          0           []                               
                                                                                                  
 embedding (Embedding)          (None, 5, 8)         1320        ['input_7[0][0]']                
                                                                                                  
 input_8 (InputLayer)           [(None, 40)]         0           []                               
                                                                                                  
 flatten (Flatten)              (None, 40)           0           ['embedding[0][0]']              
                                                                                            

In [ ]:
history = model.fit([c_item,q_embed], y_train, batch_size=8, epochs=5, validation_split = 0.2)

Epoch 1/5
100636/100636 [==============================] - 314s 3ms/step - loss: 9.9169e-04 - cosine_similarity: 0.9803 - val_loss: 0.0010 - val_cosine_similarity: 0.9800
Epoch 2/5
100636/100636 [==============================] - 309s 3ms/step - loss: 9.8832e-04 - cosine_similarity: 0.9804 - val_loss: 9.8297e-04 - val_cosine_similarity: 0.9805
Epoch 3/5
100636/100636 [==============================] - 301s 3ms/step - loss: 9.8616e-04 - cosine_similarity: 0.9804 - val_loss: 9.8086e-04 - val_cosine_similarity: 0.9805
Epoch 4/5
100636/100636 [==============================] - 299s 3ms/step - loss: 9.8375e-04 - cosine_similarity: 0.9805 - val_loss: 9.9318e-04 - val_cosine_similarity: 0.9803
Epoch 5/5
100636/100636 [==============================] - 299s 3ms/step - loss: 9.8221e-04 - cosine_similarity: 0.9805 - val_loss: 0.0010 - val_cosine_similarity: 0.9800


In [ ]:
q_embed_test = test_df['query_embedding'].values.tolist()
q_embed_test = np.array(q_embed_test).astype(np.float32)


c_item_test = test_df['enc_type'].values.tolist()
c_item_test = np.array(c_item_test).astype(np.float32)


y_test = test_df['comp_embedding'].values.tolist()
y_test = np.array(y_test).astype(np.float32)

print(y_test.shape)

(251589, 40)


In [ ]:
result = model.evaluate([c_item_test,q_embed_test],y_test)

7863/7863 [==============================] - 13s 2ms/step - loss: 0.0010 - cosine_similarity: 0.9801


In [ ]:
model.save('recommendation_model.h5')#after 50 epochs

In [ ]:
model = tf.keras.models.load_model('recommendation_model.h5')

In [ ]:
sample = X_test[:10]
predicted_probabilities = shallow_mlp_model.predict(sample)
product_names = type_test_df['product_name'].values.tolist()[:10]
ids = type_test_df['product_id'].values.tolist()[:10]

for i in range(10):
    item_id =ids[i]
    item_embedding = sample[i].reshape(1,-1)

    predicted_proba = [proba for proba in predicted_probabilities[i]]
    top_3_labels = [
        x
        for _, x in sorted(
            zip(predicted_probabilities[i], lookup.get_vocabulary()),
            key=lambda pair: pair[0],
            reverse=True,
        )
    ][:3]
    item_list =[]
    true_labels =[]
    print(f"Recommendations for "+product_names[i]+ " are : ")
    for comp_type in top_3_labels:
        knn_df = final_products[final_products['category_code'] == comp_type]
        comp_enc = knn_df['encoded_type'].values[0]
        comp_enc = np.array(comp_enc).astype(np.float32).reshape(1,-1)
        comp_embed = model.predict([comp_enc, [item_embedding]])


        # neigh = KNeighborsClassifier(n_neighbors=1, n_jobs=-1, metric ='cosine')
        # neigh.fit(list(knn_df.embedding),list(knn_df.product_id))
        # recommendation = neigh.predict(comp_embed)
        all_embeds = knn_df.embedding.values.tolist()
        best = 0.0
        for j in range(len(all_embeds)):
            sim = abs(cosine_similarity(comp_embed,all_embeds[j].reshape(1,-1)))
            if sim > best:
                best = sim
                rec_item_id = knn_df.iloc[j]['product_id']
                
            
        rec = final_products[final_products['product_id'] == rec_item_id]['product_name'].unique()
        true_label = types_df[(types_df.query_product == product_names[i]) & (types_df.comp_type == comp_type)]['comp_item'].unique()
        if len(true_label) >0:
            true_labels.append(true_label[0])
        if len(rec) > 0:
            item_list.append(rec[0])

    print(f"                 ({', '.join([item for item in item_list])})") 
    print(f"Actual Items(s): ({', '.join([item for item in true_labels])})")
    print(f"Predicted Label(s): ({', '.join([label for label in top_3_labels])})")
    # print(f"Actual Label(s):  ({', '.join([label for label in invert_multi_hot(y_test[i])])})")
    print(" ")
    


Recommendations for samsung vacuum are : 
                 (panasonic microwave, galaxy iron, vestel tv)
Actual Items(s): (samsung microwave, vitek iron, yasin tv)
Predicted Label(s): (appliances kitchen microwave, appliances iron, electronics video tv)
 
Recommendations for atlant refrigerators are : 
                 (artel vacuum, sony tv, lg washer)
Actual Items(s): (samsung vacuum, samsung tv, samsung washer)
Predicted Label(s): (appliances environment vacuum, electronics video tv, appliances kitchen washer)
 
Recommendations for doogee smartphone are : 
                 (yasin tv, apple headphone, elari clocks)
Actual Items(s): ()
Predicted Label(s): (electronics video tv, electronics audio headphone, electronics clocks)
 
Recommendations for willmark air heater are : 
                 (samsung tv, haier water heater, elenberg kettle)
Actual Items(s): (ariston water heater, willmark kettle)
Predicted Label(s): (electronics video tv, appliances environment water heater, appliances

xxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxxx

Experimentation codes